In [1]:
import pandas as pd
from functools import reduce
from tqdm import tqdm

import msgpack
import boto3
import awswrangler as wr
from io import BytesIO
import pickle
import numpy as np
import re
import datetime

import matplotlib.pyplot as plt
import seaborn as sns
import json

np.random.seed(1)

In [2]:
import warnings
warnings.filterwarnings("ignore")

# Connection

In [3]:
ACCESS_KEY='du3wAsX0uzEBBn4AdkFpCX4ZTXvSWFVG48GA4jbT'
SECRET_KEY='WA0NJOX0AFAY4K1J92XZ'

wr.config.s3_endpoint_url = 'https://obs.ru-moscow-1.hc.sbercloud.ru'

boto3.setup_default_session(
    region_name='ru-moscow',
    aws_access_key_id=SECRET_KEY,
    aws_secret_access_key=ACCESS_KEY,
)

def _get_default_boto3_client():
    return boto3.client('s3', endpoint_url=wr.config.s3_endpoint_url)

def get_object(s3_url):
    s3_client = _get_default_boto3_client()
    bucket, key = _split_3s_url_to_bucket_and_key(s3_url)
    return s3_client.get_object(Bucket=bucket, Key=key)


In [4]:
import findspark
findspark.init() 

import pyspark
from pyspark.sql import SparkSession
import pyspark.sql.functions as F
from pyspark.sql.types import IntegerType
from pyspark.ml.feature import StringIndexer, IndexToString
from pyspark.ml import Pipeline
import pandas as pd
import numpy as np
from datetime import date
from scipy import sparse

spark = SparkSession.builder.appName("Dummy").master('local').config(
    "spark.driver.memory", "100g"
).config(
    "spark.driver.cores", '16'
).config(
    "spark.kryoserializer.buffer.max", '2047'
).getOrCreate()
print("session = ", spark.getActiveSession())
config_spark_s3_adv = {
    'access_id': 'WA0NJOX0AFAY4K1J92XZ',
    'access_key': 'du3wAsX0uzEBBn4AdkFpCX4ZTXvSWFVG48GA4jbT',
    'impl': 'org.apache.hadoop.fs.s3a.S3AFileSystem',
    'endpoint': 'https://obs.ru-moscow-1.hc.sbercloud.ru'
}

spark._jsc.hadoopConfiguration().set("fs.s3a.impl", config_spark_s3_adv["impl"])
spark._jsc.hadoopConfiguration().set("fs.s3a.endpoint", config_spark_s3_adv["endpoint"])
spark._jsc.hadoopConfiguration().set("fs.s3a.access.key", config_spark_s3_adv["access_id"])
spark._jsc.hadoopConfiguration().set("fs.s3a.secret.key", config_spark_s3_adv["access_key"])
spark._jsc.hadoopConfiguration().set("fs.s3a.aws.credentials.provider", "org.apache.hadoop.fs.s3a.SimpleAWSCredentialsProvider")
spark.sparkContext.uiWebUrl

23/01/22 14:03:12 WARN Utils: Your hostname, ecs-test288 resolves to a loopback address: 127.0.1.1; using 10.11.10.114 instead (on interface eth0)
23/01/22 14:03:12 WARN Utils: Set SPARK_LOCAL_IP if you need to bind to another address
23/01/22 14:03:13 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable
Using Spark's default log4j profile: org/apache/spark/log4j-defaults.properties
Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).


session =  <pyspark.sql.session.SparkSession object at 0x7efce824dd00>


'http://10.11.10.114:4040'

# Calculating

In [5]:
kp_path = 's3://ml-okko-object-storage/cold_start/data.json'
kp_df = wr.s3.read_json(kp_path).T

In [6]:
kp_df.head(3)

kinopoisk_id    imdb_id  \
e785baa6-f175-42b4-9e16-4319ac7991d5         6580  tt0098382   
4593737e-de9c-40df-97db-fb3cf85a08ef         6460  tt0102975   
11ba66db-e941-4c3a-8da6-d8900e56f8c7      1228112  tt9469842   

                                                                 name_ru  \
e785baa6-f175-42b4-9e16-4319ac7991d5    Звездный путь 5: Последний рубеж   
4593737e-de9c-40df-97db-fb3cf85a08ef  Звездный путь 6: Неоткрытая страна   
11ba66db-e941-4c3a-8da6-d8900e56f8c7                   Дьявольская месть   

                                     name_en  \
e785baa6-f175-42b4-9e16-4319ac7991d5    None   
4593737e-de9c-40df-97db-fb3cf85a08ef    None   
11ba66db-e941-4c3a-8da6-d8900e56f8c7    None   

                                                               name_original  \
e785baa6-f175-42b4-9e16-4319ac7991d5         Star Trek V: The Final Frontier   
4593737e-de9c-40df-97db-fb3cf85a08ef  Star Trek VI: The Undiscovered Country   
11ba66db-e941-4c3a-8da6-d8900e56f8c7                         Devil's Revenge   

                                                                             poster_url  \
e785baa6-f175-42b4-9e16-4319ac7991d5  https://kinopoiskapiunofficial.tech/images/pos...   
4593737e-de9c-40df-97db-fb3cf85a08ef  https://kinopoiskapiunofficial.tech/images/pos...   
11ba66db-e941-4c3a-8da6-d8900e56f8c7  https://kinopoiskapiunofficial.tech/images/pos...   

                                                                     poster_url_preview  \
e785baa6-f175-42b4-9e16-4319ac7991d5  https://kinopoiskapiunofficial.tech/images/pos...   
4593737e-de9c-40df-97db-fb3cf85a08ef  https://kinopoiskapiunofficial.tech/images/pos...   
11ba66db-e941-4c3a-8da6-d8900e56f8c7  https://kinopoiskapiunofficial.tech/images/pos...   

                                     reviews_count rating_good_review  \
e785baa6-f175-42b4-9e16-4319ac7991d5            12               58.3   
4593737e-de9c-40df-97db-fb3cf85a08ef             9               94.4   
11ba66db-e941-4c3a-8da6-d8900e56f8c7             0               None   

                                     rating_good_review_vote_count  ...  \
e785baa6-f175-42b4-9e16-4319ac7991d5                             5  ...   
4593737e-de9c-40df-97db-fb3cf85a08ef                             8  ...   
11ba66db-e941-4c3a-8da6-d8900e56f8c7                             0  ...   

                                     editor_annotation rating_mpaa  \
e785baa6-f175-42b4-9e16-4319ac7991d5              None          pg   
4593737e-de9c-40df-97db-fb3cf85a08ef              None          pg   
11ba66db-e941-4c3a-8da6-d8900e56f8c7              None        None   

                                     rating_age_limits  \
e785baa6-f175-42b4-9e16-4319ac7991d5             age12   
4593737e-de9c-40df-97db-fb3cf85a08ef             age12   
11ba66db-e941-4c3a-8da6-d8900e56f8c7              None   

                                                       last_sync serial  \
e785baa6-f175-42b4-9e16-4319ac7991d5  2022-10-12T00:17:52.003064  False   
4593737e-de9c-40df-97db-fb3cf85a08ef  2022-11-05T02:04:00.478219  False   
11ba66db-e941-4c3a-8da6-d8900e56f8c7  2022-10-26T02:24:23.316209  False   

                                     short_film completed  \
e785baa6-f175-42b4-9e16-4319ac7991d5      False     False   
4593737e-de9c-40df-97db-fb3cf85a08ef      False     False   
11ba66db-e941-4c3a-8da6-d8900e56f8c7      False     False   

                                                                          distributions  \
e785baa6-f175-42b4-9e16-4319ac7991d5  [{'type': 'PREMIERE', 'sub_type': None, 'date'...   
4593737e-de9c-40df-97db-fb3cf85a08ef  [{'type': 'PREMIERE', 'sub_type': None, 'date'...   
11ba66db-e941-4c3a-8da6-d8900e56f8c7  [{'type': 'PREMIERE', 'sub_type': None, 'date'...   

                                                                             box_office  \
e785baa6-f175-42b4-9e16-4319ac7991d5  [{'type': 'BUDGET', 'amount': 27800000, 'curre...   
4593737e-de9c-40df-97db-fb3cf8

In [7]:
kp_df[kp_df['name_ru'].duplicated()]['name_ru'].value_counts()

Ералаш                    4
Близнецы                  3
В клетке                  3
Книга джунглей            3
Говорящий Том и друзья    3
                         ..
Обратная связь            1
Супергерои                1
Свинья                    1
Свингеры                  1
Бесконечная ночь          1
Name: name_ru, Length: 324, dtype: int64

In [8]:
data = pd.DataFrame(kp_df['description'])

In [9]:
data.isnull().sum()

description    255
dtype: int64

In [10]:
data

description
e785baa6-f175-42b4-9e16-4319ac7991d5  Кризис, разразившийся на песчаной планете Нимб...
4593737e-de9c-40df-97db-fb3cf85a08ef  После взрыва Праксиса, одной из лун Кроноса, у...
11ba66db-e941-4c3a-8da6-d8900e56f8c7  Неудачливый археолог возвращается из экспедици...
3f30a2ef-53b7-40e3-954f-1bdfc38a6d17  Эта «поджарка» была записана в Лос-Анджелесе 1...
cdfa700f-122d-41e5-b8dc-9c6813bab6d2                                               None
...                                                                                 ...
43bddcc0-db12-428e-9c65-f5606aa4b989  Рюрик, Александр Невский, Дмитрий Донской, Ива...
ac0c9152-c070-43a0-bb99-7e72764b7c0a                                               None
ce8d2906-a33f-4140-9ffe-e091990d71a4  После очередной травмы могулистка Молли Блум р...
0bfb5a13-50fc-48f3-b51a-a30971024651  Тысячи лет назад в древних историях осталось п...
6dd86e60-5d6d-475d-9b46-e989ac7a30b6  Цзян Цзыци — футболист из нашего времени, кото...

[10917 rows x 1 columns]

## Preprocessing

In [11]:
!pip install razdel
!pip install pymystem3==0.1.10

In [12]:
data.dropna()[data.dropna().duplicated(keep=False)]

description
07b6d2a6-449e-4823-813f-4f1904085c0f  Адвокат Роберт Билотт выступает с обвинением в...
87b4a82f-d6db-4e07-bae2-d98f5c3b2a03  Чёрное сердце бьётся в груди молодого короля А...
481a5a96-c7a3-411d-a7dd-2deca5526b99  История Кенни Уэллса — современного золотоиска...
14e52eb8-cfd1-4391-b8b3-8638323dcc90  Молодой д’Артаньян покинул родной дом и отправ...
9057ccb5-2c91-4669-8575-2f644c7607e4  Эксцентричный мультимиллионер подписывает согл...
...                                                                                 ...
7becd8d8-1fb8-4ee6-b903-47817686ddd8  Генри страдает редким генетическим заболевание...
e6ea57ce-52eb-465b-b9b8-270bc498ca53  Чудом уцелев после падения с 20-го этажа, мене...
62541c49-7a32-45d0-8981-44ee6968d329  О борьбе за власть между двумя ветвями дома Та...
dd125e4d-8825-4c9b-8be4-4048f571aa92  1926 год. Разгар НЭПа. Новгородский жулик Подк...
ce8d2906-a33f-4140-9ffe-e091990d71a4  После очередной травмы могулистка Молли Блум р...

[241 rows x 1 columns]

In [13]:
# data.dropna()[data.dropna().duplicated(keep=False)].groupby('description').groups

In [14]:
# '58ee7908-4c18-47d2-849e-5d45f32f3d38', '0a4d2ac4-6953-4c7f-8fbd-6be5e231fa5e' - эйфория 

In [15]:
# kp_df.loc['58ee7908-4c18-47d2-849e-5d45f32f3d38', :]

In [16]:
# kp_df.loc['0a4d2ac4-6953-4c7f-8fbd-6be5e231fa5e', :]

In [17]:
import re
from razdel import tokenize
from pymystem3 import Mystem
import nltk
from nltk.corpus import stopwords
nltk.download('stopwords')

ru_stopwords = set(stopwords.words('russian'))
ru_stopwords.add('это')
ru_stopwords.add('который')

class TextPreprocessing:
    def __init__(self, stopwords_removing=False, lemmatizing=False):
        self.stopwords_removing = stopwords_removing
        self.lemmatizing = lemmatizing
    
    def replace_backslash_n(self, texts):
        print(r'Replacing \n with whitespaces \\n...')
        pattern = re.compile('\.(\r|\n)')
        return [re.sub(pattern, '. ', text.strip()) for text in tqdm(texts)]

    def keep_cyrillic_only(self, texts):
        print('Keeping cyrillic only...')
        pattern = re.compile('[^А-Яа-яё ]')
        return [re.sub(pattern, '', text) for text in tqdm(texts)]

    def remove_backslash_n(self, texts):
        print(r'Removing \n...')
        pattern = re.compile('\n')
        return [re.sub(pattern, ' ', text.strip()) for text in tqdm(texts)]

    def tokenize(self, texts):
        print('Tokenizing...')
        return [[tokenized.text for tokenized in tokenize(text)] for text in tqdm(texts)]

    def lemmatize(self, texts):
        print('Lemmatizing...')
        lemmatizer = Mystem()
        return [''.join(lemmatizer.lemmatize(text)) for text in tqdm(texts)]

    def remove_stopwords(self, texts):
        print('Removing stopwords...')
        return [[w for w in text if w not in ru_stopwords] for text in tqdm(texts)]

    def transform(self, texts):
        texts = texts.map(lambda x: x.replace(u'\xa0', ' '))
        texts = self.replace_backslash_n(texts)
        texts = self.keep_cyrillic_only(texts)
        texts = [text.lower() for text in texts]

        if self.lemmatizing:
            texts = self.lemmatize(texts)

        texts = self.tokenize(texts)

        if self.stopwords_removing:
            texts = self.remove_stopwords(texts)

        return texts

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [16]:
df = data.dropna()
df.reset_index(drop=True, inplace=True)
preprocesser = TextPreprocessing(stopwords_removing=True, lemmatizing=True)

df_pr = preprocesser.transform(df['description'])
tokens = reduce(lambda x, y : x + y, df_pr)

Replacing \n with whitespaces \\n...


100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 10662/10662 [00:00<00:00, 289961.93it/s]


Keeping cyrillic only...


100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 10662/10662 [00:00<00:00, 107953.60it/s]

Lemmatizing...



Installing mystem to /root/.local/bin/mystem from http://download.cdn.yandex.net/mystem/mystem-3.0-linux3.1-64bit.tar.gz
100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 10662/10662 [00:22<00:00, 474.51it/s]


Tokenizing...


100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 10662/10662 [00:02<00:00, 4211.33it/s]


Removing stopwords...


100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 10662/10662 [00:00<00:00, 130424.43it/s]


In [17]:
df_pr[0]

['кризис',
 'разражаться',
 'песчаный',
 'планета',
 'нимбус',
 'располагать',
 'нейтральный',
 'зона',
 'казаться',
 'лишь',
 'акт',
 'заявление',
 'местный',
 'бунтарство',
 'желающий',
 'лишь',
 'привлекать',
 'внимание',
 'федерация',
 'повстанец',
 'лидер',
 'уроженец',
 'планета',
 'вулкан',
 'имя',
 'сайбок',
 'обладать',
 'выдающийся',
 'вулканеанский',
 'мерка',
 'парапсихологический',
 'способность',
 'достаточно',
 'лишь',
 'краткий',
 'общение',
 'человек',
 'либо',
 'инопланетянин',
 'испытывать',
 'чувство',
 'безраздельный',
 'доверие',
 'сайбок',
 'объявлять',
 'новый',
 'мессия',
 'собираться',
 'отправляться',
 'поиск',
 'думать',
 'бог',
 'некстати',
 'подвертываться',
 'рука',
 'энтерпрайз',
 'свой',
 'команда',
 'вынуждать',
 'выполнять',
 'данный',
 'миссия',
 'спока',
 'немногие',
 'поддавшисеться',
 'внушение',
 'мочь',
 'подымать',
 'рука',
 'свой',
 'родной',
 'брат',
 'путь',
 'лежать',
 'центр',
 'галактика',
 'великий',
 'барьер',
 'таинственный',
 'планета

In [18]:
df['description'][0]

'Кризис, разразившийся на песчаной планете Нимбус III (Nimbus III), расположенной в нейтральной зоне, казалось бы, был всего лишь еще одним актом заявления о себе местного бунтарства, желающем лишь привлечь внимание Федерации - но не на этот раз.\n\nТеперь у повстанцев есть лидер, уроженец планеты Вулкан по имени Сайбок (Sybok), обладающий выдающимися даже по вулканеанским меркам парапсихологическими способностями - ему достаточно лишь краткого общения для того, чтобы человек либо другой инопланетянин испытывал к нему чувство безраздельного доверия.\n\nСайбок объявляет себя новым мессией и собирается отправиться на поиски - кого бы вы думали? - Бога! И некстати подвернувшийся ему под руку «Энтерпрайз» со своей командой будет вынужден выполнить данную миссию, ведь даже Спок, один из немногих не поддавшися внушению, не может поднять руку на своего... родного брата.\r\n\r\nИх путь лежит в центр галактики, за Великий Барьер (The Great Barrier), на таинственную планету Ша Ка Ри (Sha Ka Ree)

In [19]:
pd.Series(tokens).value_counts()

свой              5464
жизнь             3401
друг              2594
год               2512
весь              2478
                  ... 
хипстерский          1
грузиться            1
транссибирский       1
царапать             1
цзися                1
Length: 33832, dtype: int64

## N-grams TBD

In [20]:
def create_n_grams(texts, n=2):
    n_grams = []

    for text in texts:
        text_n_grams = []
        for i in range(len(text)-n):
            text_n_grams.append(' ' .join(text[i:i+n]))
        n_grams.append(text_n_grams)
    return n_grams

In [21]:
# preprocesser = TextPreprocessing(stopwords_removing=False, lemmatizing=True)

# data_for_n_grams = preprocesser.transform(data.dropna()['description'])

bigrams = create_n_grams(df_pr)
bigrams = reduce(lambda x, y : x + y, bigrams)

## Refference corpus

In [22]:
from bs4 import BeautifulSoup 
import glob
from random import choices
import random
import re

random.seed(123)

In [23]:
def get_freq(text, n=1, voc=None):
    if voc is None:
        voc = set(text)
    word_freq = {}
    for word in tqdm(text):
        word_freq[word] = word_freq.get(word, n) + 1

    return word_freq

In [25]:
files = [f for f in glob.glob("/root/User/COLD_START/xmls/*.xml")]
print(f'Number of files {len(files)}')

Number of files 4007


In [26]:
files = choices(files, k=1000)

In [30]:
# Reading the data inside the xml file to a variable under the name  data
data_oc = []
for file in files:
    with open(f'{file}', 'rb') as f:  # , encoding='utf-8'
        file = f.read()
        bs_data = BeautifulSoup(file, 'xml')
        data_oc.append(bs_data.find_all('source'))

In [31]:
data_oc

[[<source>Работко</source>,
  <source>Вчера был замечательный рабочий день.</source>,
  <source>Мы молодежным коллективом в свободное время загадывали и обсуждали различные интересные задачки.</source>,
  <source>Задача 1.</source>,
  <source>Перед вами стоят три ширмы.</source>,
  <source>За двумя из них по козлу, за третьей машина, которую вы хотите выиграть.</source>,
  <source>Вы выбираете ширму, а ведущий открывает ширму, отличную от выбранной, за которой стоит козел.</source>,
  <source>Далее вам дается право поменять выбранную ширму.</source>,
  <source>После чего вы забираете свой приз.</source>,
  <source>Вопрос: стоит ли пользоваться этим правом?</source>,
  <source>Задача 2.</source>,
  <source>Перед вами стоят три корзины.</source>,
  <source>В одной яблоки, во другой апельсины, в третьей яблоки с апельсинами.</source>,
  <source>Вы не видите что в какой корзине находится.</source>,
  <source>Однако знаете, надписи, указывающие где что лежит, на корзинах перепутаны.</source

In [33]:
pattern = re.compile('</?source>')
data_oc_series = pd.Series([re.sub(pattern, '', str(sent)) for text in data_oc for sent in text])

In [34]:
preprocesser = TextPreprocessing(stopwords_removing=True, lemmatizing=True)

data_oc_norm = preprocesser.transform(data_oc_series)

Replacing \n with whitespaces \\n...


100%|████████████| 19524/19524 [00:00<00:00, 390532.51it/s]


Keeping cyrillic only...


100%|████████████| 19524/19524 [00:00<00:00, 205335.88it/s]


Lemmatizing...


100%|██████████████| 19524/19524 [00:11<00:00, 1742.37it/s]


Tokenizing...


100%|█████████████| 19524/19524 [00:01<00:00, 18625.92it/s]


Removing stopwords...


100%|████████████| 19524/19524 [00:00<00:00, 559049.64it/s]


In [35]:
# 553 sec
data_oc_norm = reduce(lambda x, y : x + y, data_oc_norm)

In [36]:
data_oc_norm

['работко',
 'вчера',
 'замечательный',
 'рабочий',
 'день',
 'молодежный',
 'коллектив',
 'свободный',
 'время',
 'загадывать',
 'обсуждать',
 'различный',
 'интересный',
 'задачка',
 'задача',
 'стоять',
 'ширма',
 'козел',
 'третий',
 'машина',
 'хотеть',
 'выигрывать',
 'выбирать',
 'ширма',
 'ведущий',
 'открывать',
 'ширма',
 'отличный',
 'выбирать',
 'стоять',
 'козел',
 'далее',
 'даваться',
 'право',
 'поменять',
 'выбирать',
 'ширма',
 'забирать',
 'свой',
 'приз',
 'вопрос',
 'стоять',
 'пользоваться',
 'право',
 'задача',
 'стоять',
 'корзина',
 'яблоко',
 'апельсин',
 'третий',
 'яблоко',
 'апельсин',
 'видеть',
 'корзина',
 'находиться',
 'однако',
 'знать',
 'надпись',
 'указывать',
 'лежать',
 'корзина',
 'перепутывать',
 'даваться',
 'право',
 'вытягивать',
 'любой',
 'корзина',
 'фрукт',
 'взглядывать',
 'корректно',
 'расставлять',
 'надпись',
 'задача',
 'домик',
 'гном',
 'ворваться',
 'тролль',
 'решать',
 'сжирать',
 'гном',
 'взмаливаться',
 'крайний',
 'мера',


In [37]:
len(data_oc_norm)

178195

## Get frequencies, calculate ratio

In [38]:
frec_oc = get_freq(data_oc_norm)

100%|█████████| 178195/178195 [00:00<00:00, 2578126.41it/s]


In [39]:
frec_oc_list = [(k, v) for k, v in frec_oc.items()]
frec_oc_list.sort(key=lambda x: x[1])
frec_oc_list[-20:]

[('являться', 307),
 ('иметь', 313),
 ('день', 332),
 ('работа', 349),
 ('место', 361),
 ('страна', 372),
 ('дело', 373),
 ('российский', 428),
 ('самый', 437),
 ('первый', 438),
 ('россия', 479),
 ('новый', 502),
 ('также', 514),
 ('становиться', 567),
 ('время', 677),
 ('человек', 755),
 ('мочь', 756),
 ('весь', 869),
 ('свой', 980),
 ('год', 1602)]

In [40]:
frec_data = get_freq(tokens)

100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 418321/418321 [00:00<00:00, 2661981.80it/s]


In [41]:
frec_data_list = [(k, v) for k, v in frec_data.items()]
frec_data_list.sort(key=lambda x: x[1])
frec_data_list[-20:]

[('семья', 1190),
 ('жить', 1194),
 ('молодой', 1270),
 ('находить', 1293),
 ('мочь', 1309),
 ('решать', 1320),
 ('история', 1401),
 ('оказываться', 1414),
 ('девушка', 1451),
 ('мир', 1643),
 ('самый', 1650),
 ('новый', 1685),
 ('время', 1725),
 ('человек', 2106),
 ('становиться', 2229),
 ('весь', 2479),
 ('год', 2513),
 ('друг', 2595),
 ('жизнь', 3402),
 ('свой', 5465)]

In [42]:
word_spec = {}

for word, freq in frec_data.items():
    word_spec[word] = freq / frec_oc.get(word, 1)

In [43]:
word_spec_list = [(k, v) for k, v in word_spec.items()]
word_spec_list.sort(key=lambda x: x[1], reverse=True)

In [44]:
pd.DataFrame(word_spec_list, columns=['Word', 'freq_rusentiment / freq_opencorpora']).head(20)# .to_csv('/content/sample_data/keywords_from_frequency.csv')

Word  freq_rusentiment / freq_opencorpora
0            джек                           147.000000
1    расследовать                           129.000000
2         подруга                           120.000000
3      ограбление                           118.000000
4            катя                           116.000000
5            макс                           115.000000
6         мечтать                           113.250000
7        отважный                           113.000000
8           фрэнк                           104.000000
9     воспитывать                            88.000000
10     супергерой                            87.000000
11   безжалостный                            86.000000
12         маньяк                            86.000000
13  эксцентричный                            85.000000
14      одержимый                            83.000000
15     влюбляться                            82.000000
16        капитан                            80.666667
17    приключение                            77.875000
18           плен                            76.000000
19        городок                            75.166667

In [45]:
keywords = pd.DataFrame(word_spec_list, columns=['token', 'freq_ratio'])

In [47]:
keywords.shape

(33832, 2)

In [48]:
keywords

token  freq_ratio
0              джек  147.000000
1      расследовать  129.000000
2           подруга  120.000000
3        ограбление  118.000000
4              катя  116.000000
...             ...         ...
33827   собственник    0.029412
33828    таможенный    0.028037
33829        диабет    0.027027
33830          млрд    0.018182
33831            рф    0.017699

[33832 rows x 2 columns]

In [46]:
keywords.to_csv('keywords.csv')

# Encoding TBD

### Can do: embeddings, ohe, tf-idf

In [18]:
keywords = pd.read_csv('keywords.csv', index_col=0)

keywords.head()

token  freq_ratio
0          джек       147.0
1  расследовать       129.0
2       подруга       120.0
3    ограбление       118.0
4          катя       116.0

In [19]:
# джек,  катя, макс, фрэнк,сэм, даша, дэнни, лизаб ана, наташа, лена, соня, уилл,
# шон, костя
# алена, джейк

In [20]:
df_keywords = data.copy(deep=True)

In [21]:
df_keywords.dropna(inplace=True)

In [22]:
df_keywords.shape

(10662, 1)

In [23]:
def encode_keywords(texts, kw):
    print(len(kw))
    preprocesser = TextPreprocessing(stopwords_removing=True, lemmatizing=True)
    texts_prepr = preprocesser.transform(texts['description'].dropna())
    print(f'len(texts_prepr): {len(texts_prepr)}')
    keywords_df = pd.DataFrame(np.full((len(texts_prepr), len(kw)), 0), columns=kw['token'], index=texts.index)
    keywords_df['texts'] = texts_prepr
    print(f'keywords_df shape: {keywords_df.shape}')
    
    for i, row in keywords_df.iterrows():
        for token in row['texts']:
            if token in list(kw['token'].values):
                keywords_df.loc[i, token] = 1
            
    return keywords_df

In [24]:
len(df_keywords)

10662

In [26]:
kws = encode_keywords(df_keywords, keywords)

33832
Replacing \n with whitespaces \\n...


100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 10662/10662 [00:00<00:00, 211819.09it/s]


Keeping cyrillic only...


100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 10662/10662 [00:00<00:00, 83483.31it/s]


Lemmatizing...


...

Tokenizing...


100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 10662/10662 [00:03<00:00, 2929.62it/s]


Removing stopwords...


100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 10662/10662 [00:00<00:00, 88630.50it/s]


len(texts_prepr): 10662
keywords_df shape: (10662, 33833)


In [27]:
kws.shape

(10662, 33833)

In [28]:
kws.to_csv('keywords_df_for_each_content.csv')

### get only 1000 1st keywords for prediction

In [ ]:
cropped_keywords = keywords[:1000]
cropped_keywords.shape

In [59]:
kws = encode_keywords(df_keywords, cropped_keywords)

1000
Replacing \n with whitespaces \\n...


100%|████████████████████████████████████████████████████████████████████████████████████| 10662/10662 [00:00<00:00, 249349.96it/s]


Keeping cyrillic only...


100%|████████████████████████████████████████████████████████████████████████████████████| 10662/10662 [00:00<00:00, 103820.56it/s]


Lemmatizing...


...

Tokenizing...


100%|██████████████████████████████████████████████████████████████████████████████████████| 10662/10662 [00:02<00:00, 4101.24it/s]


Removing stopwords...


100%|██████████████████████████████████████████████████████████████████████████████████████| 10662/10662 [00:01<00:00, 9141.17it/s]


len(texts_prepr): 10662
keywords_df shape: (10662, 1001)


In [60]:
kws.shape

(10662, 1001)

In [65]:
kws.to_csv('keywords_df_for_each_content_1000.csv')